In [36]:
import numpy as np
import yroot
import yleaf
from ytool import *

In [1]:
import gc
import psutil
import time
import numpy as np
from rur import uri, uhmi
import warnings
import logging
from ytool import *
from yroot import Treebase
from yleaf import Leaf
import importlib
import inspect
import traceback

params = importlib.import_module("params")
#########################################################
#   From params.py, record to dictionary
#########################################################
p = {}
for key in params.__dict__.keys():
    if not "_" in key:
        p[key] = params.__dict__[key]
    p["flush_GB"] = params.flush_GB
p = DotDict(p)

#########################################################
#   Load nout
#########################################################
modenames = {"hagn": "Horizon-AGN", 
            "y01605": "YZiCS-01605",
            "y04466": "YZiCS-04466",
            "y05420": "YZiCS-05420",
            "y05427": "YZiCS-05427",
            "y06098": "YZiCS-06098",
            "y07206": "YZiCS-07206",
            "y10002": "YZiCS-10002",
            "y17891": "YZiCS-17891",
            "y24954": "YZiCS-24954",
            "y29172": "YZiCS-29172",
            "y29176": "YZiCS-29176",
            "y35663": "YZiCS-35663",
            "y36413": "YZiCS-36413",
            "y36415": "YZiCS-36415",
            "y39990": "YZiCS-39990",
            "y49096": "YZiCS-49096",
            "nh": "NewHorizon",
            "nh2": "NewHorizon2",
            "nc": "NewCluster",
            "fornax": "FORNAX"
            }

# Mode configuration
mode = input("mode=? ")
if not mode in modenames.keys():
    raise ValueError(f"`{mode}` is not supported!\nSee {list(modenames.keys())}")
modename = modenames[mode]
repo, rurmode, dp = mode2repo(mode)
if dp:
    if not p.galaxy:
        dp = False
# For message printing
galstr = "Halo"
galstrs = "Halos"
if p.galaxy:
    galstr = "Galaxy"
    galstrs = "Galaxies"

# Read output list
nout = load_nout(mode=mode, galaxy=p.galaxy)
nstep = load_nstep(mode=mode, galaxy=p.galaxy, nout=nout)

#########################################################
#   Make debugger for log
#########################################################
debugger = None
# Initialize
resultdir = f"{repo}/YoungTree/"
if not os.path.isdir(resultdir):
    os.mkdir(resultdir)
fname = make_logname(mode, -1, logprefix=p.logprefix)
# repo/YoungTree/ytree_ini.log
debugger = custom_debugger(fname, detail=p.detail)
message = f"< YoungTree >\nUsing {modename} {galstr}\n{len(nout)} outputs are found! ({nout[-1]}~{nout[0]})\n\nSee `{fname}`\n\n"
debugger.info(message)
print(message)

#########################################################
###############         Data base                  ######
#########################################################
debugger.info(f"\nAllow {p.flush_GB:.2f} GB Memory")
print(f"Allow {p.flush_GB:.2f} GB Memory")

MyTree = Treebase(simmode=mode, galaxy=p.galaxy, debugger=debugger, verbose=0, flush_GB=p.flush_GB, loadall=True, detail=p.detail, logprefix=p.logprefix, dp=dp, resultdir=resultdir)


#########################################################
###############         Tree Building              ######
#########################################################
def loadout(Tree:Treebase, iout:int, resultdir=None):
    func = f"[{inspect.stack()[0][3]}]"; prefix = f"{func}({iout}) "
    clock = timer(text=prefix, verbose=Tree.verbose, debugger=Tree.debugger)

    backups=None
    if os.path.isfile(f"{resultdir}ytree_{iout:05d}.pickle"):
        backups = pklload(f"{resultdir}ytree_{iout:05d}.pickle")
    Tree.load_snap(iout, prefix=prefix)
    if backups is None:
        Tree.load_gals(iout, galid='all', return_part=True, prefix=prefix)
        Tree.load_part(iout, galid='all', prefix=prefix)
    else:
        Tree.load_gals(iout, galid='all', return_part=False, prefix=prefix)
    clock2 = timer(text=f"{prefix}[load_leaf]", verbose=Tree.verbose, debugger=Tree.debugger)
    for galid in Tree.dict_gals['galaxymakers'][iout]['id']:
        backup = None
        if (backups is not None):
            if galid in backups.keys():
                backup = backups[galid]
        Tree.load_leaf(iout, galid, backup=backup, prefix=prefix)
    clock2.done(add=f"({len(Tree.dict_gals['galaxymakers'][iout]['id'])} gals)")
    Tree.flush(iout)

    clock.done()

def find_cands(Tree:Treebase, iout:int, jout:int, mcut=0.01, resultdir=None, prefix=""):
    func = f"[{inspect.stack()[0][3]}]"; prefix = f"{prefix}{func}({iout}<->{jout}) "
    clock = timer(text=prefix, verbose=Tree.verbose, debugger=Tree.debugger)

    keys = list(Tree.dict_leaves[iout].keys())
    jhalos = Tree.part_halo_match[jout]
    backups = {}
    for key in keys:
        leaf:Leaf = Tree.dict_leaves[iout][key]
        calc = True
        if(leaf.prog is not None):
            if(jout in leaf.prog[:,0]):
                calc=False
        if(leaf.desc is not None):
            if(jout in leaf.desc[:,0]):
                calc=False
        
        if calc:
            pid = leaf.pid
            pid = pid[pid <= len(jhalos)]
            hosts = jhalos[pid-1]
            hosts = hosts[hosts>0]
            hosts, count = np.unique(hosts, return_counts=True)
            hosts = hosts[count/len(pid) > mcut]
            if len(hosts)>0:
                otherleaves = [Tree.load_leaf(jout, iid) for iid in hosts]
                ids, scores = leaf.calc_score(jout, otherleaves)
            else:
                ids = np.array([[jout, 0]])
                scores = np.array([[-10, -10, -10, -10, -10]])

            if jout<iout:
                leaf.prog = ids if leaf.prog is None else np.vstack((leaf.prog, ids))
                leaf.prog_score = scores if leaf.prog_score is None else np.vstack((leaf.prog_score, scores))
            elif jout>iout:
                leaf.desc = ids if leaf.desc is None else np.vstack((leaf.desc, ids))
                leaf.desc_score = scores if leaf.desc_score is None else np.vstack((leaf.desc_score, scores))
            else:
                raise ValueError(f"Same output {iout} and {jout}!")
        
        else:
            if jout<iout:
                arg = leaf.prog[:,0]==jout
                ids = leaf.prog[arg]
                scores = leaf.prog_score[arg]
            elif jout>iout:
                arg = leaf.desc[:,0]==jout
                ids = leaf.desc[arg]
                scores = leaf.desc_score[arg]
            else:
                raise ValueError(f"Same output {iout} and {jout}!")
            
        backups[key] = leaf.selfsave()
        dprint_(f"{prefix}<{leaf.name()}> has {len(ids)} candidates", Tree.debugger)
        if len(ids)>0:
            if np.sum(scores[0])>0:
                if len(ids) < 6:
                    dprint_(f"{prefix} {[f'{ids[i][-1]}({scores[i][0]:.3f})' for i in range(len(ids))]}", Tree.debugger)
                else:
                    dprint_(f"{prefix} {[f'{ids[i]}({scores[i][0]:.3f})' for i in range(5)]+['...']}", Tree.debugger)
    pklsave(backups, f"{resultdir}ytree_{iout:05d}.pickle", overwrite=True)

    clock.done()

uri.timer.verbose=0
for iout in nout:
    try:
        skip = False
        backups = None
        if os.path.isfile(f"{resultdir}ytree_{iout:05d}.pickle"):
            backups = pklload(f"{resultdir}ytree_{iout:05d}.pickle")
            if not p.overwrite:
                skip=True
        if not skip:
            # New log file
            fname = make_logname(MyTree.simmode, iout, logprefix=MyTree.logprefix)
            MyTree.debugger.handlers = []
            MyTree.debugger = custom_debugger(fname, detail=MyTree.detail)
            # Load snap gal part
            dprint_(f"\n\nStart at iout={iout}\n", MyTree.debugger)
            loadout(MyTree, iout, resultdir=resultdir)
            istep = out2step(iout, galaxy=p.galaxy, mode=mode, nout=nout, nstep=nstep)
            for j in range(p.nsnap):
                jstep = istep-j-1
                if jstep > 0:
                    jout = step2out(jstep, galaxy=p.galaxy, mode=mode, nout=nout, nstep=nstep)
                    dprint_(f"\n\nProgenitor at jout={jout}\n", MyTree.debugger)
                    loadout(MyTree, jout, resultdir=resultdir)
                    find_cands(MyTree, iout, jout, resultdir=resultdir)
            for j in range(p.nsnap):
                jstep = istep+j+1
                if jstep <= np.max(nstep):
                    jout = step2out(jstep, galaxy=p.galaxy, mode=mode, nout=nout, nstep=nstep)
                    if not jout in MyTree.dict_snap.keys():
                        dprint_(f"\n\nDescendant at jout={jout}\n", MyTree.debugger)
                        loadout(MyTree, jout, resultdir=resultdir)
                        find_cands(MyTree, iout, jout, resultdir=resultdir)
            
            MyTree.debugger.info(f"\n{MyTree.summary()}\n")

            cutstep = istep+5
            if cutstep<=np.max(nstep):
                cutout = step2out(cutstep, galaxy=p.galaxy, mode=mode, nout=nout, nstep=nstep)
                outs = list(MyTree.dict_leaves.keys())
                for out in outs:
                    if out > cutout:
                        MyTree.flush(out, leafclear=True)        
    except Exception as e:
        print(traceback.format_exc())
        print(e)
        MyTree.debugger.error(traceback.format_exc())
        MyTree.debugger.error(e)
        MyTree.debugger.error(MyTree.summary())
        raise ValueError("Iteration is terminated")

< YoungTree >
Using YZiCS-07206 Galaxy
178 outputs are found! (10~187)

See `/storage3/Clusters/07206/YoungTree/ytree_ini_2.log`


Allow 200.00 GB Memory
Traceback (most recent call last):
  File "/tmp/ipykernel_13053/2408752353.py", line 212, in <cell line: 189>
    find_cands(MyTree, iout, jout, resultdir=resultdir)
  File "/tmp/ipykernel_13053/2408752353.py", line 176, in find_cands
    backups[key] = leaf.selfsave()
  File "/home/jeon/YoungTree2/yleaf.py", line 110, in selfsave
    self.cat = np.record( np.rec.array(tuple(lis), dtype=dtype) )
  File "/home/jeon/.conda/envs/jeonpy/lib/python3.10/site-packages/numpy/core/records.py", line 1069, in array
    return fromarrays(obj, dtype=dtype, shape=shape, **kwds)
  File "/home/jeon/.conda/envs/jeonpy/lib/python3.10/site-packages/numpy/core/records.py", line 676, in fromarrays
    raise ValueError(f'array-shape mismatch in array {k} ("{name}")')
ValueError: array-shape mismatch in array 14 ("prog")

array-shape mismatch in array 14 ("

ValueError: Iteration is terminated

In [7]:
leaf = MyTree.load_leaf(187, 1)

In [6]:
backup_keys = ["nparts", "id", "timestep", "aexp", "m", "x", "y", "z", "vx", "vy", "vz", "r", "rvir", "mvir"]

In [26]:
leaf.prog.shape

(1, 2)

In [39]:
tuple(leaf.prog)

(array([186,   1]),)

In [42]:
tuple(leaf.prog).shape

AttributeError: 'tuple' object has no attribute 'shape'

In [28]:
leaf.prog.astype(object).shape

(1, 2)

In [43]:
lis[0].tolist

<function int32.tolist>

In [73]:
# lis = [ia for ia,ib in zip(leaf.cat, leaf.cat.dtype.names) if ib in backup_keys] + [leaf.prog] + [leaf.prog_score] + [leaf.desc] + [leaf.desc_score]
lis = [ia for ia,ib in zip(leaf.cat, leaf.cat.dtype.names) if ib in backup_keys] + [leaf.prog] + [leaf.prog_score] + [leaf.desc] + [leaf.desc_score]
lis

[97589,
 1,
 187,
 1.0000004,
 45520646000.0,
 0.23176348,
 0.38772473,
 0.51713234,
 217.0606,
 320.15793,
 59.54777,
 0.0016857174,
 0.00021619833,
 13069278000.0,
 array([[186,   1]]),
 array([[3.71421078, 0.94807649, 0.89189886, 0.92340109, 0.95083433]]),
 None,
 None]

In [81]:
# dtype = np.dtype([idtype for idtype in leaf.cat.dtype.descr if idtype[0] in backup_keys] + [('prog',np.ndarray), ("prog_score",  'O'), ('desc','O'), ("desc_score",  'O')])
dtype = [idtype for idtype in leaf.cat.dtype.descr if idtype[0] in backup_keys] + [('prog',np.ndarray), ("prog_score",  'O'), ('desc','O'), ("desc_score",  'O')]
dtype

[('nparts', '<i4'),
 ('id', '<i4'),
 ('timestep', '<i4'),
 ('aexp', '<f4'),
 ('m', '<f4'),
 ('x', '<f4'),
 ('y', '<f4'),
 ('z', '<f4'),
 ('vx', '<f4'),
 ('vy', '<f4'),
 ('vz', '<f4'),
 ('r', '<f4'),
 ('rvir', '<f4'),
 ('mvir', '<f4'),
 ('prog', numpy.ndarray),
 ('prog_score', 'O'),
 ('desc', 'O'),
 ('desc_score', 'O')]

In [83]:
arr = np.empty(1, dtype=dtype)[0]
arr, arr.dtype

((0, 0, 0, 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., None, None, None, None),
 dtype([('nparts', '<i4'), ('id', '<i4'), ('timestep', '<i4'), ('aexp', '<f4'), ('m', '<f4'), ('x', '<f4'), ('y', '<f4'), ('z', '<f4'), ('vx', '<f4'), ('vy', '<f4'), ('vz', '<f4'), ('r', '<f4'), ('rvir', '<f4'), ('mvir', '<f4'), ('prog', 'O'), ('prog_score', 'O'), ('desc', 'O'), ('desc_score', 'O')]))

In [84]:
for i, ilis in enumerate(lis):
    arr[i] =  ilis
arr, arr.dtype

((97589, 1, 187, 1.0000004, 4.5520646e+10, 0.23176348, 0.38772473, 0.51713234, 217.0606, 320.15793, 59.54777, 0.00168572, 0.0002162, 1.3069278e+10, array([[186,   1]]), array([[3.71421078, 0.94807649, 0.89189886, 0.92340109, 0.95083433]]), None, None),
 dtype([('nparts', '<i4'), ('id', '<i4'), ('timestep', '<i4'), ('aexp', '<f4'), ('m', '<f4'), ('x', '<f4'), ('y', '<f4'), ('z', '<f4'), ('vx', '<f4'), ('vy', '<f4'), ('vz', '<f4'), ('r', '<f4'), ('rvir', '<f4'), ('mvir', '<f4'), ('prog', 'O'), ('prog_score', 'O'), ('desc', 'O'), ('desc_score', 'O')]))

In [85]:
type(arr)

numpy.void

In [72]:
np.rec.fromarrays(tuple(lis), dtype=dtype)

ValueError: array-shape mismatch in array 15 ("prog_score")

In [37]:
from rur import uri, uhmi

In [38]:
import os

In [46]:
backups = pklload("/storage3/Clusters/07206/YoungTree/ytree_00187.pickle")

In [47]:
backups.keys()

dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 22

In [49]:
backups[40]['gal']

(426, 40, 187, 1.0000004, 2.0048038e+08, 0.24124652, 0.40723023, 0.5344872, 121.98702, -55.336258, 238.60292, 0.00017711, 1.98547e-05, 10209648., {186: array([[186,  41]]), 185: array([[185,  46]]), 184: array([[184,  40]]), 183: None, 182: None}, {186: array([3.70917209]), 185: array([3.04258033]), 184: array([2.97501656]), 183: None, 182: None}, {}, {})

In [34]:
brick1 = os.listdir("/storage6/NewHorizon/halo/")
brick1 = [int(brick[11:]) for brick in brick1 if brick.startswith("tree_bricks")]
brick1 = np.sort(brick1)
brick2 = os.listdir("/storage6/NewHorizon/halo/DM/")
brick2 = [int(brick[11:]) for brick in brick2 if brick.startswith("tree_bricks")]
brick2 = np.sort(brick2)
brick3 = os.listdir("/storage6/NewHorizon/halo_iap/")
brick3 = [int(brick[11:]) for brick in brick3 if brick.startswith("tree_bricks")]
brick3 = np.sort(brick3)

In [2]:
Tree = yroot.Treebase(simmode='y07206', galaxy=True)

[__Treebase__] START
[__Treebase__] Done (0.169 sec)


In [3]:
Tree.load_part(187, galid='all')

Age of the universe (now/z=0): 13.741 / 13.741 Gyr, z = -0.00000 (a = 1.0000)
Reading 768 part files (2.136 GiB) in /storage3/Clusters/07206/snapshots/output_00187... 
Done (1.941s).


{1: Particle({'table': array([(0.2316548 , 0.38741355, 0.51697089, 0.0121909 , 0.01752267,  0.00274601, 5.3821419e-13,       2, 426, 1),
        (0.23174787, 0.38778033, 0.51717319, 0.0116061 , 0.01759497,  0.00531494, 5.3821419e-13,       3, 426, 1),
        (0.23182707, 0.38748244, 0.51728557, 0.0087013 , 0.01565425,  0.00404563, 5.3821419e-13,       6, 426, 1),
        ...,
        (0.23131845, 0.38769553, 0.51710034, 0.00996344, 0.02597294, -0.0049445 , 5.3821419e-13, 7626671, 426, 1),
        (0.23143167, 0.38794853, 0.51663666, 0.01168979, 0.02551574, -0.00516019, 5.3821419e-13, 7627045, 426, 1),
        (0.23136306, 0.38846187, 0.5162314 , 0.01196059, 0.02330185, -0.00317346, 5.3821419e-13, 7628663, 426, 1)],
       dtype=[('x', '<f8'), ('y', '<f8'), ('z', '<f8'), ('vx', '<f8'), ('vy', '<f8'), ('vz', '<f8'), ('m', '<f8'), ('id', '<i4'), ('cpu', '<i4'), ('haloids', '<i8')]), 'snap': <rur.uri.RamsesSnapshot object at 0x7f9086269ed0>, 'ptype': 'star'}),
 2: Particle({'table': array

In [6]:
a,b,c = Tree.load_gal(187, galid='all', return_part=True, return_galids=True)

In [7]:
b

array([      2,       3,       6, ..., 7776217, 8057869, 8148381],
      dtype=int32)

In [8]:
c

array([  1,   1,   1, ..., 248, 248, 248], dtype=int32)

In [3]:
Tree.load_part(187,1)

Age of the universe (now/z=0): 13.741 / 13.741 Gyr, z = -0.00000 (a = 1.0000)
Reading 3 part files (111.0 MiB) in /storage3/Clusters/07206/snapshots/output_00187... 
Done (0.131s).


Particle({'table': array([(0.2319697 , 0.38809174, 0.51762551, 0.01359338, 0.02252414, 0.00535714, 5.3821419e-13, 1381456, 426),
       (0.23193386, 0.38740356, 0.51760576, 0.01135379, 0.01164667, 0.00306451, 5.3821419e-13,  440376, 426),
       (0.23192022, 0.38803655, 0.51764703, 0.00884101, 0.0214863 , 0.00777358, 5.3821419e-13,  466198, 426),
       ...,
       (0.23132584, 0.38874488, 0.51596508, 0.0119924 , 0.01849014, 0.00042376, 5.3821419e-13, 1228755, 426),
       (0.23136311, 0.38876749, 0.5160414 , 0.01136013, 0.02024227, 0.00050616, 5.3821419e-13, 6311241, 426),
       (0.23135775, 0.38876408, 0.51604659, 0.01126869, 0.02108485, 0.00040373, 5.3821419e-13, 6981120, 426)],
      dtype=[('x', '<f8'), ('y', '<f8'), ('z', '<f8'), ('vx', '<f8'), ('vy', '<f8'), ('vz', '<f8'), ('m', '<f8'), ('id', '<i4'), ('cpu', '<i4')]), 'snap': <rur.uri.RamsesSnapshot object at 0x7f05838f8a00>, 'ptype': 'star'})

In [4]:
pd = Tree.load_snap(187).part_data

In [5]:
a = np.zeros(len(pd))

In [6]:
from numpy.lib.recfunctions import append_fields
pd = append_fields(pd, "test", a, usemask=False)

In [7]:
pd

array([(0.22421275, 0.38655183, 0.5083136 , -0.00311822, 0.0110907 ,  0.00680978, 5.3821419e-13, 4677296, 424, 0.),
       (0.22460728, 0.38643844, 0.50783272, -0.00333376, 0.01253109,  0.00794232, 5.3821419e-13, 6820432, 424, 0.),
       (0.22647865, 0.38509703, 0.50921966,  0.01791731, 0.01696564,  0.00306105, 5.3821419e-13, 4178442, 424, 0.),
       ...,
       (0.21780498, 0.38933272, 0.51800641,  0.01592598, 0.00789852, -0.00937069, 5.3821419e-13, 3042828, 426, 0.),
       (0.21854356, 0.38086449, 0.50303614,  0.01816429, 0.01479467, -0.00607426, 5.3821419e-13,  748117, 426, 0.),
       (0.21866288, 0.38086985, 0.50350532,  0.01814926, 0.01493866, -0.00519782, 5.3821419e-13, 6119004, 426, 0.)],
      dtype=[('x', '<f8'), ('y', '<f8'), ('z', '<f8'), ('vx', '<f8'), ('vy', '<f8'), ('vz', '<f8'), ('m', '<f8'), ('id', '<i4'), ('cpu', '<i4'), ('test', '<f8')])

In [4]:
ileaf = Tree.load_leaf(187, 1)
jleaf1 = Tree.load_leaf(186, 1)
jleaf2 = Tree.load_leaf(186, 2)
jleaf3 = Tree.load_leaf(186, 3)

Age of the universe (now/z=0): 13.672 / 13.741 Gyr, z = 0.00502 (a = 0.9950)
Reading 3 part files (136.6 MiB) in /storage3/Clusters/07206/snapshots/output_00186... 
Done (0.154s).
Searching for extra files...
Reading 2 part files (119.9 MiB) in /storage3/Clusters/07206/snapshots/output_00186... 
Done (0.188s).
Searching for extra files...
Reading 393 part files (544.9 MiB) in /storage3/Clusters/07206/snapshots/output_00186... 
Done (1.928s).


In [5]:
ileaf.calc_score(186, [jleaf1, jleaf2, jleaf3])

(array([[186,   1],
        [186,   2],
        [186,   3]]),
 array([ 3.71421078, -1.60475498, -1.66287729]))

In [6]:
ileaf.saved_matchrate, ileaf.saved_veloffset

({186: {1: (0.9480764876649789,
    array([ True,  True,  True, ..., False, False,  True])),
   2: (-1, array([False, False, False, ..., False, False, False])),
   3: (-1, array([False, False, False, ..., False, False, False]))}},
 {186: {1: 0.9234010919277233, 2: 0, 3: 0}})